<h2>Chapter1: Gathering information of the list of Stations in Tokyo</h2>

In [1]:
#Importing libraries
from bs4 import BeautifulSoup
import requests
import pandas as pd
import numpy as np

In [2]:
#Importing libraries
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


In [3]:
#To Get all stations list in Tokyo
url_list = ['https://en.wikipedia.org/wiki/Category:Railway_stations_in_Tokyo', 
            'https://en.wikipedia.org/w/index.php?title=Category:Railway_stations_in_Tokyo&pagefrom=Kasai+Station#mw-pages', 
            'https://en.wikipedia.org/w/index.php?title=Category:Railway_stations_in_Tokyo&pagefrom=Okachimachi+Station#mw-pages', 
           'https://en.wikipedia.org/w/index.php?title=Category:Railway_stations_in_Tokyo&pagefrom=Tsukishima+Station#mw-pages']
def get_station_name_list(url_list):
    name_list = []
    for url in url_list:
        source = requests.get(url)
        html = BeautifulSoup(source.content, 'lxml')
        station_name_list = html.find('div', class_='mw-category')
        station_name = station_name_list.find_all('a')
        for a in station_name:
            name_list.append(a.string)
    return name_list

In [4]:
#Make the list by calling the function
name_list = get_station_name_list(url_list)

In [5]:
#Get latitude and longitude information through geopy

def get_geo_info(name_list):
    geolocator = Nominatim(user_agent="my-application", timeout=10)
    station_lst = []
    lati_lst = []
    lon_lst = []
    failed_lst = []
    for station_name in name_list:
        try:
            location = geolocator.geocode(station_name)
            latitude = location.latitude
            longitude = location.longitude
            station_lst.append(station_name)
            lati_lst.append(latitude)
            lon_lst.append(longitude)
        except:
            failed_lst.append(station_name)
        
    return station_lst, lati_lst, lon_lst, failed_lst

In [6]:
#Get the information by calling the function
station_lst, lati_lst, lon_lst, failed_lst = get_geo_info(name_list)

In [7]:
#Make a dataframe by using the results
df = pd.DataFrame({'station':station_lst, 'latitude':lati_lst, 'longitude':lon_lst})

In [8]:
df.head()

station   latitude   longitude
0       Adachi-Odai Station  35.754678  139.770388
1            Aihara Station  35.606878  139.331680
2           Akabane Station  35.778139  139.720800
3  Akabane-iwabuchi Station  35.783147  139.720044
4      Akabanebashi Station  35.654970  139.743892

In [9]:
df.tail()

station   latitude   longitude
623        Yūrakuchō Station  35.675591  139.763305
624  Yushima Station (Tokyo)  35.708034  139.769806
625          Yūtenji Station  35.637575  139.691042
626        Zoshigaya Station  35.720260  139.714846
627          Zōshiki Station  35.550055  139.715197

<h2>Chapter2: Getting venue information of each station</h2>
**In this chapter, I will call FourSquare API and get venue information of each station.**

In [10]:
#Make a map of Tokyo
address = 'Tokyo'
geolocator1 = Nominatim()
location = geolocator1.geocode(address)
latitude = location.latitude
longitude = location.longitude

map_tokyo = folium.Map(location=[latitude, longitude], zoom_start=10)


for lat, lng, station in zip(df['latitude'], df['longitude'], df['station']):
    label=station
    label=folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False
    ).add_to(map_tokyo)
    
map_tokyo

/anaconda3/envs/UdacityDL/lib/python3.6/site-packages/ipykernel_launcher.py:3: DeprecationWarning: Using Nominatim with the default "geopy/1.18.1" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  This is separate from the ipykernel package so we can avoid doing imports until


In [11]:
#Foursquare API Information

CLIENT_ID = 'KDCNWHDEJ4UYTSB3QHKSYWIS1JX0WZI50JRRQT540WXZSP2A' # your Foursquare ID
CLIENT_SECRET = 'DCA1AC0AGG020VE1TFXXCTNS4FEULN4R520AUM4ZE5MLFQMN' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('My credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

My credentails:
CLIENT_ID: KDCNWHDEJ4UYTSB3QHKSYWIS1JX0WZI50JRRQT540WXZSP2A
CLIENT_SECRET:DCA1AC0AGG020VE1TFXXCTNS4FEULN4R520AUM4ZE5MLFQMN


In [12]:
#function that extract the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list)==0:
        return None
    else:
        return categories_list[0]['name']

In [13]:
def getNearbyVenues(names, latitude, longitude, radius=500, LIMIT=100):
    venues_list=[]
    for name, lat, lng in zip(names, latitude, longitude):
        url='https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
        
        results = requests.get(url).json()['response']['groups'][0]['items']
        
        venues_list.append([(
            name,
            lat,
            lng,
            v['venue']['name'],
            v['venue']['location']['lat'],
            v['venue']['location']['lng'],
            v['venue']['categories'][0]['name']
                            ) for v in results])
        
        
    nearby_venues=pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns=['station',
                           'station Latitude',
                           'station Longitude',
                           'Venue',
                           'Venue Latitude',
                           'Venue Longitude',
                           'Venue Category'
        
    ]
    return (nearby_venues)

In [14]:
tokyo_venues = getNearbyVenues(df['station'], df['latitude'], df['longitude'])

In [15]:
tokyo_venues.shape

(26951, 7)

In [11]:
tokyo_venues = pd.read_csv('tokyo_venues_r500_l100.csv')

In [16]:
tokyo_venues.head()

station  station Latitude  station Longitude  \
0  Adachi-Odai Station         35.754678         139.770388   
1  Adachi-Odai Station         35.754678         139.770388   
2  Adachi-Odai Station         35.754678         139.770388   
3  Adachi-Odai Station         35.754678         139.770388   
4  Adachi-Odai Station         35.754678         139.770388   

                         Venue  Venue Latitude  Venue Longitude  \
0                オーケーストア 足立小台店       35.755243       139.768456   
1  MOS Burger (モスバーガー 島忠足立小台店)       35.755219       139.768133   
2             洋食レストラン 山惣(やまそう)       35.750813       139.768882   
3       K's Denki (ケーズデンキ 足立店)       35.754701       139.770530   
4                 らーめん蔵芸 足立小台店       35.755220       139.768331   

         Venue Category  
0           Supermarket  
1  Fast Food Restaurant  
2            Restaurant  
3     Electronics Store  
4      Ramen Restaurant

<h2>Capter3: Data Processing and Clustering</h2>
**In this chapter, I will cluster areas in Toronto, by the following steps:**
 
- Changing the data frame into one-hot encoding style
- Using K Means method

In [17]:
#change the data into one hot encoding style
tokyo_onehot = pd.get_dummies(tokyo_venues['Venue Category'], prefix='', prefix_sep='')
tokyo_onehot['station'] = tokyo_venues['station']

fixed_columns=[tokyo_onehot.columns[-1]] + list(tokyo_onehot.columns[:-1])
tokyo_onehot = tokyo_onehot[fixed_columns]

tokyo_onehot.head()

station  ATM  Acai House  Accessories Store  Adult Boutique  \
0  Adachi-Odai Station    0           0                  0               0   
1  Adachi-Odai Station    0           0                  0               0   
2  Adachi-Odai Station    0           0                  0               0   
3  Adachi-Odai Station    0           0                  0               0   
4  Adachi-Odai Station    0           0                  0               0   

   Afghan Restaurant  African Restaurant  Airport  Airport Food Court  \
0                  0                   0        0                   0   
1                  0                   0        0                   0   
2                  0                   0        0                   0   
3                  0                   0        0                   0   
4                  0                   0        0                   0   

   Airport Lounge  Airport Service  Airport Terminal  American Restaurant  \
0               0                0                 0                    0   
1               0                0                 0                    0   
2               0                0                 0                    0   
3               0                0                 0                    0   
4               0                0                 0                    0   

   Antique Shop  Aquarium  Arcade  Argentinian Restaurant  Art Gallery  \
0             0         0       0                       0            0   
1             0         0       0                       0            0   
2             0         0       0                       0            0   
3             0         0       0                       0            0   
4             0         0       0                       0            0   

   Art Museum  Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0           0                    0                 0                   0   
1           0                    0                 0                   0   
2           0                    0                 0                   0   
3           0                    0                 0                   0   
4           0                    0                 0                   0   

   Auditorium  Australian Restaurant  Auto Garage  Auto Workshop  BBQ Joint  \
0           0                      0            0              0          0   
1           0                      0            0              0          0   
2           0                      0            0              0          0   
3           0                      0            0              0          0   
4           0                      0            0              0          0   

   Baby Store  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0           0           0       0     0    0               0   
1           0           0       0     0    0               0   
2           0           0       0     0    0               0   
3           0           0       0     0    0               0   
4           0           0       0     0    0               0   

   Baseball Stadium  Basketball Court  Bath House  Beach  Bed & Breakfast  \
0                 0                 0           0      0                0   
1                 0                 0           0      0                0   
2                 0                 0           0      0                0   
3                 0                 0           0      0                0   
4                 0                 0           0      0                0   

   Beer Bar  Beer Garden  Beer Store  Beijing Restaurant  \
0         0            0           0                   0   
1         0            0           0                   0   
2         0            0           0                   0   
3         0            0           0                   0   
4         0            0           0                   0   

   Belarusian Restaurant  Belgian Restaurant  Betting Shop

In [18]:
tokyo_grouped = tokyo_onehot.groupby(['station']).sum().reset_index()
tokyo_grouped.head()

station  ATM  Acai House  Accessories Store  \
0       Adachi-Odai Station    0           0                  0   
1            Aihara Station    0           0                  0   
2           Akabane Station    0           0                  0   
3  Akabane-iwabuchi Station    0           0                  0   
4      Akabanebashi Station    0           0                  0   

   Adult Boutique  Afghan Restaurant  African Restaurant  Airport  \
0               0                  0                   0        0   
1               0                  0                   0        0   
2               0                  0                   0        0   
3               0                  0                   0        0   
4               0                  0                   0        0   

   Airport Food Court  Airport Lounge  Airport Service  Airport Terminal  \
0                   0               0                0                 0   
1                   0               0                0                 0   
2                   0               0                0                 0   
3                   0               0                0                 0   
4                   0               0                0                 0   

   American Restaurant  Antique Shop  Aquarium  Arcade  \
0                    0             0         0       0   
1                    0             0         0       0   
2                    0             0         0       1   
3                    0             0         0       1   
4                    1             0         0       0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Auditorium  Australian Restaurant  \
0                 0                   0           0                      0   
1                 0                   0           0                      0   
2                 0                   0           0                      0   
3                 0                   0           0                      0   
4                 0                   0           0                      0   

   Auto Garage  Auto Workshop  BBQ Joint  Baby Store  Bagel Shop  Bakery  \
0            0              0          0           0           0       0   
1            0              0          0           0           0       1   
2            0              0          3           0           1       1   
3            0              0          2           0           0       0   
4            0              0          0           0           0       1   

   Bank  Bar  Baseball Field  Baseball Stadium  Basketball Court  Bath House  \
0     0    0               0                 0                 0           0   
1     0    0               0                 0                 0           0   
2     0    3               0                 0                 0           0   
3     0    1               0                 0                 0           1   
4     0    0               0                 0                 0           0   

   Beach  Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  \
0      0                0         0            0           0   
1      0                0         0            0           0   
2      0                0         0            0           0   
3      0                0         0            0           0   
4      0                0         0            1           0   

   Beijing Restaurant  Belarusian Restaurant  Belgian Restaurant  \
0                   0                      0                   0   
1                

In [19]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [20]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

columns = ['station', 'total number of venues']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))
        
neighbourhoods_venues_sorted = pd.DataFrame(columns=columns)
neighbourhoods_venues_sorted['station'] = tokyo_grouped['station']
neighbourhoods_venues_sorted['total number of venues'] = tokyo_venues.groupby(['station']).count().reset_index().iloc[:,1]

for ind in np.arange(tokyo_grouped.shape[0]):
    neighbourhoods_venues_sorted.iloc[ind, 2:] = return_most_common_venues(tokyo_grouped.iloc[ind, :], num_top_venues)
    
neighbourhoods_venues_sorted

station  total number of venues  \
0                              Adachi-Odai Station                       7   
1                                   Aihara Station                      16   
2                                  Akabane Station                     100   
3                         Akabane-iwabuchi Station                      59   
4                             Akabanebashi Station                      57   
5                        Akado-shōgakkōmae Station                      23   
6                          Akasaka-mitsuke Station                      86   
7                             Akebonobashi Station                      79   
8                                  Akigawa Station                      13   
9                                Akihabara Station                     100   
10                                Akishima Station                       9   
11                          Akitsu Station (Tokyo)                      60   
12                           Anamori-inari Station                      46   
13                                     Aoi Station                      19   
14                                    Aomi Station                      41   
15                          Aomono-yokochō Station                      46   
16                                    Aoto Station                      36   
17                          Aoyama-itchōme Station                      71   
18                         Araiyakushi-mae Station                      23   
19                        Arakawa-itchūmae Station                      40   
20                       Arakawa-nanachōme Station                      46   
21                         Arakawa-nichōme Station                      20   
22                        Arakawa-shakomae Station                      36   
23                          Ariake Station (Tokyo)                      75   
24                   Ariake-tennis-no-mori Station                      13   
25                                 Asagaya Station                      60   
26                            Asakusabashi Station                      49   
27                               Asukayama Station                      47   
28                                Awajichō Station                     100   
29                                   Ayase Station                      64   
30                             Azabu-juban Station                     100   
31                         Bakuro-yokoyama Station                     100   
32                               Bakurochō Station                      90   
33                             Bubaigawara Station                      49   
34                              Chidorichō Station                      20   
35                     Chikatetsu-Akatsuka Station                      44   
36                     Chikatetsu-Narimasu Station                      63   
37                       Chitose-Funabashi Station                      49   
38                      Chitose-karasuyama Station                      67   
39                           Chōfu Station (Tokyo)                      33   
40             Chūō-Daigaku-Meisei-Daigaku Station                      10   
41                           Daiba Station (Tokyo)                     100   
42                             Daikan-yama Station                     100   
43                          Daimon Station (Tokyo)                      76   
44                               Daishimae Station                      19   
45                              Daitabashi Station                      39   
46                            Den-en-chōfu Station                      33   
47                          Ebara-Nakanobu Station                      50   
48                           Ebisu Station (Tokyo)                     100   
49                                 Edogawa Station                      19   
50                            Edogawabashi Station               

In [33]:
#Cluster the data
kclusters = 6

tokyo_group_clustering = tokyo_grouped.drop('station', axis=1)

kmeans = KMeans(kclusters, random_state=0).fit(tokyo_group_clustering)

kmeans.labels_[:10]

array([0, 0, 5, 4, 4, 4, 1, 5, 0, 2], dtype=int32)

In [34]:
print(df.shape)
print(kmeans.labels_.shape)

(628, 3)
(620,)


In [35]:
#add cluster labels to the columns
neighbourhoods_venues_sorted['Cluster Label'] = kmeans.labels_
neighbourhoods_venues_sorted

station  total number of venues  \
0                              Adachi-Odai Station                       7   
1                                   Aihara Station                      16   
2                                  Akabane Station                     100   
3                         Akabane-iwabuchi Station                      59   
4                             Akabanebashi Station                      57   
5                        Akado-shōgakkōmae Station                      23   
6                          Akasaka-mitsuke Station                      86   
7                             Akebonobashi Station                      79   
8                                  Akigawa Station                      13   
9                                Akihabara Station                     100   
10                                Akishima Station                       9   
11                          Akitsu Station (Tokyo)                      60   
12                           Anamori-inari Station                      46   
13                                     Aoi Station                      19   
14                                    Aomi Station                      41   
15                          Aomono-yokochō Station                      46   
16                                    Aoto Station                      36   
17                          Aoyama-itchōme Station                      71   
18                         Araiyakushi-mae Station                      23   
19                        Arakawa-itchūmae Station                      40   
20                       Arakawa-nanachōme Station                      46   
21                         Arakawa-nichōme Station                      20   
22                        Arakawa-shakomae Station                      36   
23                          Ariake Station (Tokyo)                      75   
24                   Ariake-tennis-no-mori Station                      13   
25                                 Asagaya Station                      60   
26                            Asakusabashi Station                      49   
27                               Asukayama Station                      47   
28                                Awajichō Station                     100   
29                                   Ayase Station                      64   
30                             Azabu-juban Station                     100   
31                         Bakuro-yokoyama Station                     100   
32                               Bakurochō Station                      90   
33                             Bubaigawara Station                      49   
34                              Chidorichō Station                      20   
35                     Chikatetsu-Akatsuka Station                      44   
36                     Chikatetsu-Narimasu Station                      63   
37                       Chitose-Funabashi Station                      49   
38                      Chitose-karasuyama Station                      67   
39                           Chōfu Station (Tokyo)                      33   
40             Chūō-Daigaku-Meisei-Daigaku Station                      10   
41                           Daiba Station (Tokyo)                     100   
42                             Daikan-yama Station                     100   
43                          Daimon Station (Tokyo)                      76   
44                               Daishimae Station                      19   
45                              Daitabashi Station                      39   
46                            Den-en-chōfu Station                      33   
47                          Ebara-Nakanobu Station                      50   
48                           Ebisu Station (Tokyo)                     100   
49                                 Edogawa Station                      19   
50                            Edogawabashi Station               

In [36]:
#merge basic data with sorted data frame
tokyo_merged = df
tokyo_merged = tokyo_merged.merge(neighbourhoods_venues_sorted, on='station', how='left')
tokyo_merged

station   latitude   longitude  \
0                              Adachi-Odai Station  35.754678  139.770388   
1                                   Aihara Station  35.606878  139.331680   
2                                  Akabane Station  35.778139  139.720800   
3                         Akabane-iwabuchi Station  35.783147  139.720044   
4                             Akabanebashi Station  35.654970  139.743892   
5                        Akado-shōgakkōmae Station  35.742861  139.769042   
6                          Akasaka-mitsuke Station  35.678216  139.735659   
7                             Akebonobashi Station  35.692389  139.722861   
8                                  Akigawa Station  35.728711  139.231226   
9                                Akihabara Station  35.698565  139.773056   
10                                Akishima Station  35.702480  139.350065   
11                          Akitsu Station (Tokyo)  35.778504  139.496717   
12                           Anamori-inari Station  35.550297  139.746746   
13                                     Aoi Station  35.772109  139.820465   
14                                    Aomi Station  35.624779  139.781202   
15                          Aomono-yokochō Station  35.608874  139.743075   
16                                    Aoto Station  35.745572  139.856123   
17                          Aoyama-itchōme Station  35.671999  139.725183   
18                         Araiyakushi-mae Station  35.715691  139.672657   
19                        Arakawa-itchūmae Station  35.733717  139.788930   
20                       Arakawa-nanachōme Station  35.741991  139.784140   
21                         Arakawa-nichōme Station  35.738674  139.784665   
22                        Arakawa-shakomae Station  35.750898  139.752787   
23                          Ariake Station (Tokyo)  35.634560  139.793268   
24                   Ariake-tennis-no-mori Station  35.640126  139.788861   
25                                 Asagaya Station  35.704840  139.635472   
26                            Asakusabashi Station  35.697337  139.786230   
27                               Asukayama Station  35.752283  139.737056   
28                                Awajichō Station  35.695129  139.767457   
29                                   Ayase Station  35.761603  139.824035   
30                             Azabu-juban Station  35.656496  139.736133   
31                         Bakuro-yokoyama Station  35.692111  139.782778   
32                               Bakurochō Station  35.693350  139.782453   
33                             Bubaigawara Station  35.668477  139.468506   
34                              Chidorichō Station  35.572899  139.691551   
35                     Chikatetsu-Akatsuka Station  35.769913  139.644122   
36                     Chikatetsu-Narimasu Station  35.776657  139.631302   
37                       Chitose-Funabashi Station  35.647385  139.623820   
38                      Chitose-karasuyama Station  35.668031  139.600869   
39                           Chōfu Station (Tokyo)  35.598137  139.667319   
40             Chūō-Daigaku-Meisei-Daigaku Station  35.641866  139.408762   
41                           Daiba Station (Tokyo)  35.625902  139.771422   
42                             Daikan-yama Station  35.648207  139.703262   
43                          Daimon Station (Tokyo)  35.656794  139.754692   
44                               Daishimae Station  35.778875  139.781463   
45                              Daitabashi Station  35.671155  139.659604   
46                            Den-en-chōfu Station  35.598137  139.667319   
47                          Ebara-Nakanobu Station  35.609955  139.711953   
48                           Ebisu Station (Tokyo)  35.646580  139.710215   
49                                 Edogawa Station  35.737751  139.896051   
50                            Edogawabashi Station  35.709522  139.733581   
51                               Eifuku

In [37]:
#give label to columns that have NaN values
for i in range(len(tokyo_merged)):
    if np.isnan(tokyo_merged.iloc[i, -1]):
        tokyo_merged.iloc[i, -1] = kclusters

In [38]:
#change the datatype of Cluster Labels columns into int64
tokyo_merged['Cluster Label'] = tokyo_merged['Cluster Label'].astype(np.int64)
tokyo_merged

station   latitude   longitude  \
0                              Adachi-Odai Station  35.754678  139.770388   
1                                   Aihara Station  35.606878  139.331680   
2                                  Akabane Station  35.778139  139.720800   
3                         Akabane-iwabuchi Station  35.783147  139.720044   
4                             Akabanebashi Station  35.654970  139.743892   
5                        Akado-shōgakkōmae Station  35.742861  139.769042   
6                          Akasaka-mitsuke Station  35.678216  139.735659   
7                             Akebonobashi Station  35.692389  139.722861   
8                                  Akigawa Station  35.728711  139.231226   
9                                Akihabara Station  35.698565  139.773056   
10                                Akishima Station  35.702480  139.350065   
11                          Akitsu Station (Tokyo)  35.778504  139.496717   
12                           Anamori-inari Station  35.550297  139.746746   
13                                     Aoi Station  35.772109  139.820465   
14                                    Aomi Station  35.624779  139.781202   
15                          Aomono-yokochō Station  35.608874  139.743075   
16                                    Aoto Station  35.745572  139.856123   
17                          Aoyama-itchōme Station  35.671999  139.725183   
18                         Araiyakushi-mae Station  35.715691  139.672657   
19                        Arakawa-itchūmae Station  35.733717  139.788930   
20                       Arakawa-nanachōme Station  35.741991  139.784140   
21                         Arakawa-nichōme Station  35.738674  139.784665   
22                        Arakawa-shakomae Station  35.750898  139.752787   
23                          Ariake Station (Tokyo)  35.634560  139.793268   
24                   Ariake-tennis-no-mori Station  35.640126  139.788861   
25                                 Asagaya Station  35.704840  139.635472   
26                            Asakusabashi Station  35.697337  139.786230   
27                               Asukayama Station  35.752283  139.737056   
28                                Awajichō Station  35.695129  139.767457   
29                                   Ayase Station  35.761603  139.824035   
30                             Azabu-juban Station  35.656496  139.736133   
31                         Bakuro-yokoyama Station  35.692111  139.782778   
32                               Bakurochō Station  35.693350  139.782453   
33                             Bubaigawara Station  35.668477  139.468506   
34                              Chidorichō Station  35.572899  139.691551   
35                     Chikatetsu-Akatsuka Station  35.769913  139.644122   
36                     Chikatetsu-Narimasu Station  35.776657  139.631302   
37                       Chitose-Funabashi Station  35.647385  139.623820   
38                      Chitose-karasuyama Station  35.668031  139.600869   
39                           Chōfu Station (Tokyo)  35.598137  139.667319   
40             Chūō-Daigaku-Meisei-Daigaku Station  35.641866  139.408762   
41                           Daiba Station (Tokyo)  35.625902  139.771422   
42                             Daikan-yama Station  35.648207  139.703262   
43                          Daimon Station (Tokyo)  35.656794  139.754692   
44                               Daishimae Station  35.778875  139.781463   
45                              Daitabashi Station  35.671155  139.659604   
46                            Den-en-chōfu Station  35.598137  139.667319   
47                          Ebara-Nakanobu Station  35.609955  139.711953   
48                           Ebisu Station (Tokyo)  35.646580  139.710215   
49                                 Edogawa Station  35.737751  139.896051   
50                            Edogawabashi Station  35.709522  139.733581   
51                               Eifuku

In [39]:
#create a map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=10)

#set color scheme for the clusters
x=np.arange(kclusters+1)
ys=[i+x+(i*x)**2 for i in range(kclusters+1)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

#create a map
for lat, lon, poi, cluster in zip(tokyo_merged['latitude'], tokyo_merged['longitude'], tokyo_merged['station'], tokyo_merged['Cluster Label']):
    label = folium.Popup(str(poi) + 'Cluster' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster)-1],
        fill=True,
        fill_color=rainbow[int(cluster)-1],
        fill_opacity=0.7
    ).add_to(map_clusters)
    
map_clusters

<h2>Chapter 4: Conclusion and Observation</h2>

**In this chapter, I will see how station areas in Tokyo can be clustered. The following are the groups:**

- Cluster Label 0: Suburb areas for living
- Cluster Label 1: Central eating areas
- Cluster Label 2: Central areas to hang out
- Cluster Label 3: Drinking areas¶
- Cluster Label 4: Places for living in middle-central areas
- Cluster Label 5: Places for living in central areas
- Cluster Label 6: Countryside areas

<h3>Cluster Label 0: Suburb areas for living.</h3>
**These areas have convenience stores and restaurants. Also, the total numbers of venues are mostly less than 30. These areas are not very busy, and should be places where people live.**

In [40]:
tokyo_merged.loc[tokyo_merged['Cluster Label'] ==0, tokyo_merged.columns[[0] + list(range(3, tokyo_merged.shape[1]))]]

station  total number of venues  \
0                    Adachi-Odai Station                     7.0   
1                         Aihara Station                    16.0   
8                        Akigawa Station                    13.0   
10                      Akishima Station                     9.0   
13                           Aoi Station                    19.0   
14                          Aomi Station                    41.0   
21               Arakawa-nichōme Station                    20.0   
24         Ariake-tennis-no-mori Station                    13.0   
34                    Chidorichō Station                    20.0   
39                 Chōfu Station (Tokyo)                    33.0   
40   Chūō-Daigaku-Meisei-Daigaku Station                    10.0   
46                  Den-en-chōfu Station                    33.0   
49                       Edogawa Station                    19.0   
53                     Etchūjima Station                    35.0   
54                 Fuchū Station (Tokyo)                     5.0   
58                   Fujimigaoka Station                    22.0   
60             Fune-no-kagakukan Station                    33.0   
61                         Fussa Station                    18.0   
63                     Futamatao Station                     6.0   
64                      Gaiemmae Station                    51.0   
66                Gakushuinshita Station                    21.0   
71                       Gotanno Station                    29.0   
72                      Gōtokuji Station                    24.0   
74                      Hachiōji Station                     9.0   
75             Hachiōji-Minamino Station                    27.0   
76                      Hagiyama Station                     9.0   
78                  Hakonegasaki Station                    14.0   
80                       Hamacho Station                    41.0   
83                        Hamura Station                     8.0   
95            Hatchōbori Station (Tokyo)                    49.0   
96                      Hatonosu Station                    10.0   
98                Hazama Station (Tokyo)                    49.0   
103                Higashi-Akiru Station                     6.0   
104                Higashi-Azuma Station                    12.0   
105                Higashi-fuchū Station                    31.0   
106              Higashi-Fushimi Station                    22.0   
107                Higashi-Fussa Station                    25.0   
109            Higashi-Ikebukuro Station                    32.0   
110   Higashi-ikebukuro-yonchome Station                    29.0   
119             Higashi-Nakagami Station                    19.0   
123                Higashi-ojima Station                    24.0   
124                  Higashi-Ōme Station                    17.0   
126                  Hikarigaoka Station                    50.0   
127                    Hikawadai Station                    15.0   
129                   Hinatawada Station                     5.0   
133           Hirayamajōshi-kōen Station                     7.0   
135          Hitotsubashi-Gakuen Station                    11.0   
136                     Hodokubo Station                     2.0   
140             Honjo-azumabashi Station                    35.0   
141                     Horikiri Station                    18.0   
142              Horikirishōbuen Station                    22.0   
146                    Iidabashi Station                    62.0   
150                      Ikenoue Station                    53.0   
151                    Ikusabata Station                     4.0   
152                        Inagi Station                    15.0   
155              Inokashira-kōen Station                    16.0   
156                         Iogi Station                    18.0   
158                  Ishigamimae Station                     4.0   
159                  

<h3>Cluster Label 1: Central eating areas.</h3>
**These areas have many restaurants. Each place have many restaurants.**

In [41]:
tokyo_merged.loc[tokyo_merged['Cluster Label'] ==1, tokyo_merged.columns[[0] + list(range(3, tokyo_merged.shape[1]))]]

station  total number of venues  \
6        Akasaka-mitsuke Station                    86.0   
17        Aoyama-itchōme Station                    71.0   
30           Azabu-juban Station                   100.0   
42           Daikan-yama Station                   100.0   
43        Daimon Station (Tokyo)                    76.0   
48         Ebisu Station (Tokyo)                   100.0   
68         Ginza-itchōme Station                   100.0   
82          Hamamatsuchō Station                   100.0   
89              Hanzōmon Station                    83.0   
102               Hibiya Station                   100.0   
108        Higashi-ginza Station                   100.0   
134                Hiroo Station                    95.0   
170           Kagurazaka Station                    92.0   
195            Kayabachō Station                    75.0   
233            Kōjimachi Station                    83.0   
254           Kudanshita Station                    62.0   
296        Mitsukoshimae Station                   100.0   
323          Naka-Meguro Station                   100.0   
340           Nihombashi Station                   100.0   
341         Nijūbashimae Station                   100.0   
342            Ningyōchō Station                   100.0   
352        Nishi-Ogikubo Station                   100.0   
355       Nishi-Shinjuku Station                   100.0   
359       Nishi-Taishidō Station                    89.0   
369             Nogizaka Station                   100.0   
407     Ōtemachi Station (Tokyo)                   100.0   
418             Roppongi Station                   100.0   
419     Roppongi-itchōme Station                   100.0   
430          Sangen-Jaya Station                   100.0   
455            Shibakoen Station                    72.0   
460              Shibuya Station                   100.0   
486      Shin-Nihombashi Station                   100.0   
506  Shintomichō Station (Tokyo)                   100.0   
519          Suitengūmae Station                   100.0   
537            Takaracho Station                   100.0   
547      Tamachi Station (Tokyo)                    54.0   
552        Tameike-Sannō Station                   100.0   
575      Toranomon Hills Station                    90.0   
576            Toranomon Station                   100.0   
583              Tsukiji Station                   100.0   
584         Tsukijishijō Station                    87.0   
600  Ushigome-kagurazaka Station                   100.0   
618               Yoyogi Station                   100.0   
621        Yoyogi-Uehara Station                    92.0   

    1st Most Common Venue 2nd Most Common Venue   3rd Most Common Venue  \
6     Japanese Restaurant                 Hotel                    Café   
17     Italian Restaurant     Convenience Store     Japanese Restaurant   
30    Japanese Restaurant       Soba Restaurant      Italian Restaurant   
42    Japanese Restaurant                  Café                Boutique   
43    Japanese Restaurant             BBQ Joint      Chinese Restaurant   
48    Japanese Restaurant             BBQ Joint                     Bar   
68     Italian Restaurant   Japanese Restaurant                    Café   
82    Japanese Restaurant     Convenience Store             Coffee Shop   
89    Japanese Restaurant    Italian Restaurant         Soba Restaurant   
102   Japanese Restaurant              Sake Bar        Sushi Restaurant   
108   Japanese Restaurant      Ramen Restaurant                    Café   
134                  Café     Convenience Store     Japanese Restaurant   
170   Japanese Restaurant    Italian Restaurant       Convenience Store   
195      Ramen Restaurant       Soba Restaurant     Japanese Restaurant   
233   Japanese Restaurant    Italian Restaurant         Soba Restaurant   
254   Japanese Restaurant      Ramen Restaurant                    Café   
296   Japanese Restaurant                 Hotel  

<h3>Cluster Label 2:  Central areas to hang out</h3>
**These area has Cafe and Coffee Shops. Also, they have shopping places like Stores and Shops. Manu of he total number of venues are 100. These areas seem to be visited for hanging out.**

In [42]:
tokyo_merged.loc[tokyo_merged['Cluster Label'] ==2, tokyo_merged.columns[[0] + list(range(3, tokyo_merged.shape[1]))]]

station  total number of venues  \
9                                Akihabara Station                   100.0   
25                                 Asagaya Station                    60.0   
41                           Daiba Station (Tokyo)                   100.0   
62                         Futako-Tamagawa Station                   100.0   
65                         Gakugei-daigaku Station                    45.0   
67                                   Ginza Station                   100.0   
85        Haneda Airport Domestic Terminal Station                    67.0   
86   Haneda Airport International Terminal Station                    51.0   
87               Haneda Airport Terminal 1 Station                    65.0   
88               Haneda Airport Terminal 2 Station                    63.0   
90                                Harajuku Station                   100.0   
165                               Jimbōchō Station                   100.0   
166                      Jiyūgaoka Station (Tokyo)                    91.0   
210                              Kichijōji Station                   100.0   
271                            Manseibashi Station                   100.0   
276                         Meiji-jingumae Station                   100.0   
285                        Minami-Shinjuku Station                   100.0   
305                               Mukōhara Station                    48.0   
372                             Ochanomizu Station                    85.0   
400                             Omotesandō Station                   100.0   
443                                Sendagi Station                    53.0   
470                         Shimo-kitazawa Station                   100.0   
487                        Shin-Ochanomizu Station                   100.0   
499                               Shinjuku Station                   100.0   
500                      Shinjuku-gyoemmae Station                   100.0   
515                     Suehirocho Station (Tokyo)                   100.0   
555                    Tawaramachi Station (Tokyo)                    76.0   
572                         Tokyo Teleport Station                   100.0   
619                        Yoyogi-Hachiman Station                    49.0   
623                              Yūrakuchō Station                   100.0   

    1st Most Common Venue 2nd Most Common Venue      3rd Most Common Venue  \
9       Electronics Store            Hobby Shop                   Sake Bar   
25                   Café    Italian Restaurant           Ramen Restaurant   
41            Coffee Shop                  Café        Japanese Restaurant   
62                   Café         Shopping Mall                  BBQ Joint   
65                   Café      Ramen Restaurant                   Sake Bar   
67                   Café        Clothing Store        Japanese Restaurant   
85         Airport Lounge           Coffee Shop                       Café   
86         Airport Lounge                  Café            Udon Restaurant   
87         Airport Lounge           Coffee Shop                       Café   
88         Airport Lounge           Coffee Shop                       Café   
90                   Café        Clothing Store                Coffee Shop   
165                  Café      Ramen Restaurant  Japanese Curry Restaurant   
166                  Café          Dessert Shop         Italian Restaurant   
210                  Café      Ramen Restaurant                   Tea Room   
271     Electronics Store            Hobby Shop                       Café   
276                  Café        Clothing Store                Coffee Shop   
285   Japanese Restaurant          Dessert Shop                Coffee Shop   
305                  Café   Japanese Restaurant           Ramen Restaurant   
372                  Café     Electronics Store                Coffee Shop   
400                  Café              Boutique        Japanese 

<h3>Cluster Label 3: Drinking areas</h3>
**These areas have many sake bars, and many of their total numbers of venues are 100. These seem to be drinking places in the central area.**

In [43]:
tokyo_merged.loc[tokyo_merged['Cluster Label'] ==3, tokyo_merged.columns[[0] + list(range(3, tokyo_merged.shape[1]))]]

station  total number of venues  \
28              Awajichō Station                   100.0   
70               Gotanda Station                   100.0   
147            Ikebukuro Station                   100.0   
162           Iwamotocho Station                   100.0   
172       Kamata Station (Tokyo)                    71.0   
186        Kanda Station (Tokyo)                   100.0   
207          Keisei Ueno Station                   100.0   
212            Kinshichō Station                   100.0   
229               Kōenji Station                   100.0   
263     Kyōbashi Station (Tokyo)                   100.0   
309       Musashi-Koyama Station                    61.0   
324     Naka-Okachimachi Station                   100.0   
378   Ogawamachi Station (Tokyo)                   100.0   
383              Ōimachi Station                    88.0   
389          Okachimachi Station                   100.0   
435       Seibu-Shinjuku Station                   100.0   
465            Shimbashi Station                   100.0   
501  Shinjuku-Nishiguchi Station                   100.0   
502    Shinjuku-sanchōme Station                   100.0   
505              Shinsen Station                   100.0   
507             Shiodome Station                    72.0   
518           Suidōbashi Station                   100.0   
527       Tachikawa-Kita Station                   100.0   
529         Takadanobaba Station                    82.0   
589        Uchisaiwaicho Station                   100.0   
590                 Ueno Station                   100.0   
591        Ueno-hirokoji Station                   100.0   
592     Ueno-okachimachi Station                   100.0   
617     Yotsuya-sanchōme Station                    76.0   
624      Yushima Station (Tokyo)                   100.0   

    1st Most Common Venue      2nd Most Common Venue    3rd Most Common Venue  \
28       Ramen Restaurant                   Sake Bar                     Café   
70    Japanese Restaurant                   Sake Bar                      Bar   
147              Sake Bar           Ramen Restaurant                     Café   
162              Sake Bar           Ramen Restaurant      Japanese Restaurant   
172      Ramen Restaurant        Japanese Restaurant                 Sake Bar   
186              Sake Bar           Ramen Restaurant               Hobby Shop   
207              Sake Bar                  BBQ Joint      Japanese Restaurant   
212      Ramen Restaurant                   Sake Bar              Coffee Shop   
229              Sake Bar           Ramen Restaurant                     Café   
263      Ramen Restaurant                       Café  South Indian Restaurant   
309              Sake Bar           Ramen Restaurant                BBQ Joint   
324              Sake Bar                  BBQ Joint         Ramen Restaurant   
378      Ramen Restaurant  Japanese Curry Restaurant              Coffee Shop   
383      Ramen Restaurant          Convenience Store      Japanese Restaurant   
389              Sake Bar                  BBQ Joint         Ramen Restaurant   
435      Ramen Restaurant                   Sake Bar                BBQ Joint   
465              Sake Bar        Japanese Restaurant       Seafood Restaurant   
501              Sake Bar           Ramen Restaurant                      Bar   
502                   Bar                  BBQ Joint                 Sake Bar   
505   Japanese Restaurant                   Sake Bar                Nightclub   
507              Sake Bar         Seafood Restaurant                BBQ Joint   
518      Ramen Restaurant                 Steakhouse                    Hotel   
527      Ramen Restaurant        Japanese Restaurant              Coffee Shop   
529      Ramen Restaurant                   Sake Bar      Tonkatsu Restaurant   
589              Sake Bar        Japanese Restaurant                BBQ Joint   
590              Sake Bar        Japanese Restaurant      

<h3>Cluster Label 4: Places for living in middle-central areas.</h3>
**These areas have mostly between 40 and 60. These areas have Convenience Stores and Restaurants.**

In [44]:
tokyo_merged.loc[tokyo_merged['Cluster Label'] ==4, tokyo_merged.columns[[0] + list(range(3, tokyo_merged.shape[1]))]]

station  total number of venues  \
3          Akabane-iwabuchi Station                    59.0   
4              Akabanebashi Station                    57.0   
5         Akado-shōgakkōmae Station                    23.0   
11           Akitsu Station (Tokyo)                    60.0   
12            Anamori-inari Station                    46.0   
15           Aomono-yokochō Station                    46.0   
16                     Aoto Station                    36.0   
18          Araiyakushi-mae Station                    23.0   
19         Arakawa-itchūmae Station                    40.0   
20        Arakawa-nanachōme Station                    46.0   
22         Arakawa-shakomae Station                    36.0   
26             Asakusabashi Station                    49.0   
27                Asukayama Station                    47.0   
33              Bubaigawara Station                    49.0   
35      Chikatetsu-Akatsuka Station                    44.0   
36      Chikatetsu-Narimasu Station                    63.0   
37        Chitose-Funabashi Station                    49.0   
44                Daishimae Station                    19.0   
45               Daitabashi Station                    39.0   
47           Ebara-Nakanobu Station                    50.0   
50             Edogawabashi Station                    49.0   
51                Eifukuchō Station                    23.0   
52                    Ekoda Station                    52.0   
55                     Fuda Station                    22.0   
56                 Fudō-mae Station                    31.0   
57                Fujimidai Station                    28.0   
59                 Funabori Station                    46.0   
69                 Gokokuji Station                    30.0   
73             Hachimanyama Station                    44.0   
77                  Haijima Station                    24.0   
79          Hakusan Station (Tokyo)                    47.0   
81               Hamadayama Station                    38.0   
84             Hana-Koganei Station                    29.0   
91                   Hasune Station                    22.0   
92                 Hasunuma Station                    34.0   
94                Hatanodai Station                    49.0   
97                 Hatsudai Station                    60.0   
99         Heiwadai Station (Tokyo)                    35.0   
100               Heiwajima Station                    41.0   
101     Hibarigaoka Station (Tokyo)                    40.0   
111            Higashi-Jūjō Station                    44.0   
112        Higashi-Kitazawa Station                    31.0   
113          Higashi-Kōenji Station                    51.0   
114         Higashi-Koganei Station                    44.0   
115          Higashi-Kurume Station                    32.0   
116       Higashi-matsubara Station                    37.0   
117        Higashi-Murayama Station                    35.0   
118        Higashi-Nagasaki Station                    27.0   
120          Higashi-Nakano Station                    55.0   
122    Higashi-ogu-sanchōme Station                    33.0   
125        Higashi-Mukōjima Station                    27.0   
130            Hino Station (Tokyo)                    39.0   
132           Hirai Station (Tokyo)                    53.0   
137            Hon-komagome Station                    39.0   
138                Hōnanchō Station                    40.0   
139          Hongō-sanchōme Station                    36.0   
143                    Hōya Station                    34.0   
144                Ichigaya Station                    58.0   
145                 Ichinoe Station                    35.0   
148                 Ikegami Station                    39.0   
149          Ikejiri-Ōhashi Station                    41.0   
153          Inagi-Naganuma Station                    19.0   
154                Inarichō Station                    39.0

<h3>Cluster Label 5: Places for living in central areas.</h3>
**These areas have mostly between 70 and 100. These areas have Convenience Stores and Restaurants. These areas seem to be busy, but many people seem to live there.**

In [45]:
tokyo_merged.loc[tokyo_merged['Cluster Label'] ==5, tokyo_merged.columns[[0] + list(range(3, tokyo_merged.shape[1]))]]

station  total number of venues  \
2                   Akabane Station                   100.0   
7              Akebonobashi Station                    79.0   
23           Ariake Station (Tokyo)                    75.0   
29                    Ayase Station                    64.0   
31          Bakuro-yokoyama Station                   100.0   
32                Bakurochō Station                    90.0   
38       Chitose-karasuyama Station                    67.0   
93                 Hatagaya Station                    87.0   
121      Higashi-nihombashi Station                    79.0   
128                Hikifune Station                    46.0   
157           Iriya Station (Tokyo)                    57.0   
167            Jūjō Station (Tokyo)                    61.0   
185               Kanamechō Station                    43.0   
191          Kasuga Station (Tokyo)                   100.0   
192    Kasumigaseki Station (Tokyo)                   100.0   
196           Keikyū Kamata Station                    71.0   
202         Keisei Hikifune Station                    45.0   
220              Kita-Senju Station                   100.0   
228              Kodemmachō Station                   100.0   
232                   Koiwa Station                    59.0   
235       Kokkai-gijidō-mae Station                    79.0   
239         Kokusai-Tenjijō Station                    75.0   
240  Kokusai-tenjijō-seimon Station                   100.0   
244        Komazawa-daigaku Station                    52.0   
262                 Kuramae Station                    82.0   
264                   Kyōdō Station                    69.0   
302          Monzen-Nakachō Station                   100.0   
308         Musashi-Koganei Station                    74.0   
334                Narimasu Station                    70.0   
361            Nishi-waseda Station                    84.0   
373          Ochiai Station (Tokyo)                    61.0   
380                 Ogikubo Station                   100.0   
385             Ōji Station (Tokyo)                    53.0   
397           Ōmori Station (Tokyo)                   100.0   
402                Onarimon Station                   100.0   
404                Ōokayama Station                    59.0   
420                 Ryōgoku Station                    75.0   
432                Sasazuka Station                    82.0   
483              Shin-Koiwa Station                    49.0   
517           Sugamoshinden Station                    61.0   
528        Tachikawa-Minami Station                   100.0   
561                Tochōmae Station                   100.0   
580                 Tōyōchō Station                    96.0   
582                  Toyosu Station                   100.0   

    1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
2                Sake Bar     Convenience Store      Ramen Restaurant   
7       Convenience Store              Sake Bar      Ramen Restaurant   
23      Convenience Store   Japanese Restaurant                  Café   
29      Convenience Store      Ramen Restaurant              Pharmacy   
31      Convenience Store       Bed & Breakfast   Japanese Restaurant   
32      Convenience Store       Bed & Breakfast           Coffee Shop   
38      Convenience Store              Sake Bar    Chinese Restaurant   
93      Convenience Store      Ramen Restaurant    Chinese Restaurant   
121     Convenience Store   Japanese Restaurant       Bed & Breakfast   
128     Convenience Store      Ramen Restaurant           Coffee Shop   
157     Convenience Store      Ramen Restaurant   Japanese Restaurant   
167     Convenience Store              Sake Bar      Ramen Restaurant   
185     Convenience Store      Ramen Restaurant            Restaurant   
191     Convenience Store      Baseball Stadium      Ramen Restaurant   
192     Convenience Store           Coffee Shop   Japanese Restaurant   
196     Convenience Stor

<h3>Cluster Label 6: Country side areas</h3>
**These places have no venue.**

In [46]:
tokyo_merged.loc[tokyo_merged['Cluster Label'] ==6, tokyo_merged.columns[[0] + list(range(3, tokyo_merged.shape[1]))]]

station  total number of venues 1st Most Common Venue  \
131    Hinode Station                     NaN                   NaN   
189     Kasai Station                     NaN                   NaN   
248      Kori Station                     NaN                   NaN   
251    Kosuge Station                     NaN                   NaN   
325  Nakagami Station                     NaN                   NaN   
392   Okusawa Station                     NaN                   NaN   
433     Sawai Station                     NaN                   NaN   
608      Yaho Station                     NaN                   NaN   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
131                   NaN                   NaN                   NaN   
189                   NaN                   NaN                   NaN   
248                   NaN                   NaN                   NaN   
251                   NaN                   NaN                   NaN   
325                   NaN                   NaN                   NaN   
392                   NaN                   NaN                   NaN   
433                   NaN                   NaN                   NaN   
608                   NaN                   NaN                   NaN   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
131                   NaN                   NaN                   NaN   
189                   NaN                   NaN                   NaN   
248                   NaN                   NaN                   NaN   
251                   NaN                   NaN                   NaN   
325                   NaN                   NaN                   NaN   
392                   NaN                   NaN                   NaN   
433                   NaN                   NaN                   NaN   
608                   NaN                   NaN                   NaN   

    8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  \
131                   NaN                   NaN                    NaN   
189                   NaN                   NaN                    NaN   
248                   NaN                   NaN                    NaN   
251                   NaN                   NaN                    NaN   
325                   NaN                   NaN                    NaN   
392                   NaN                   NaN                    NaN   
433                   NaN                   NaN                    NaN   
608                   NaN                   NaN                    NaN   

     Cluster Label  
131              6  
189              6  
248              6  
251              6  
325              6  
392              6  
433              6  
608              6